# API Usage Notebook

This notebook explains how to use the apps API to create, deploy, and manage apps in Databricks.

## Set up

In [ ]:
# Execute this cell to get the host and token necessary to call the REST API
# This cell should be run in a Databricks notebook
host = dbutils.notebook.entry_point.getDbutils().notebook().getContext().apiUrl().getOrElse(None)
token = dbutils.notebook.entry_point.getDbutils().notebook().getContext().apiToken().getOrElse(None)

import requests
import json
import time

headers = {
    "Authorization": "Bearer " + token,
}
host

In [ ]:
# the app name needs to be DNS safe. No spaces. Only lowercase letters, numbers and hyphens
app_name = "nyc-taxi-app" 
# this is the path to the workspace folder with the source code
source_code_path = f"/Workspace/Shared/lakehouse-apps/{app_name}"
# nice description on what the app does
app_description = "App example with NYC Taxi data"

## Create app

In [ ]:
# Creating a new app creates the app identity - a service principal, oauth, and DNS entry
# Once the app is created, we can use the app identity for development.

url = host + "/api/2.0/preview/apps"
data = {
  "name": app_name,
  "description": app_description,
}
response = requests.post(url, headers=headers, json=data)
response.json()

In [ ]:

# It should only take a few seconds for the app to be created. 
# You can check the status of the app creation with the following code:

url = host + f"/api/2.0/preview/apps/{app_name}"

response = requests.get(url, headers=headers)
response_dict = json.loads(response.text)

response_dict


## Deploy app

In [ ]:
# Once the app is created, we can deploy the app. This will create a deployment and a compute target for the app. 
# The deployment will be in the "In Progress" state until the deployment is ready. 
# This can take a few minutes if we have to provision a new container. 
# After the container is provisioned, it should only take a few seconds to deploy the app again.

url = host + f"/api/2.0/preview/apps/{app_name}/deployments"
data = {
  "source_code_path": source_code_path
}
response = requests.post(url, headers=headers, json=data)
response_dict = json.loads(response.text)
deployment_id = response_dict.get("deployment_id")
response_dict

In [ ]:
# The first time the app is deployed, it can take a couple of minutes to deploy the app. 
# You can wait for the deployment to complete with the following code:

url = host + f"/api/2.0/preview/apps/{app_name}/deployments/{deployment_id}"

for _ in range(10):
    time.sleep(1)
    response = requests.get(url, headers=headers)
    response_dict = json.loads(response.text)
    if response_dict.get("status").get("state") != "IN_PROGRESS":
        break
    else:
        print("Deployment in progress. Status: ", response_dict.get("status").get("state"))
response_dict

## Get app info or list all apps

In [ ]:
# Get app info
url = host + f"/api/2.0/preview/apps/{app_name}"

response = requests.get(url, headers=headers)
response.json()

In [ ]:
# List all apps
url = host + "/api/2.0/preview/apps"

response = requests.get(url, headers=headers)
response.json()

## Stop and Start the app

In [ ]:
url = host + f"/api/2.0/preview/apps/{app_name}/stop"

response = requests.post(url, headers=headers)
response.json()

In [ ]:
url = host + f"/api/2.0/preview/apps/{app_name}/start"

response = requests.post(url, headers=headers)
response.json()

## Delete the app

In [ ]:
url = host + "/api/2.0/preview/apps"

print(f"Delete app {app_name}")

resp = requests.delete(host + f"/api/2.0/preview/apps/{app_name}", headers=headers)
response.json()